## Linear Regresson of Standardization

In [1]:
import pandas as pd
import numpy as np
import warnings
import csv
warnings.filterwarnings('ignore')

In [2]:
df = pd.read_csv("s3://datasetairbnb/airbnb_cleaned.csv")

In [3]:
import statsmodels.api as sm
from sklearn import linear_model
from sklearn.linear_model import LinearRegression, Ridge, Lasso
from sklearn.model_selection import cross_val_score
from sklearn.model_selection import train_test_split

In [4]:
def standardize_col(col):
    mean = np.mean(col)
    std = np.std(col)
    return col.apply(lambda x: (x - mean) / std)

non_cat_vars = ['accommodates', 'bedrooms', 'beds', 'number_of_reviews', 'availability_30', 'minimum_nights', 'bathrooms']
for col in non_cat_vars:
    df[col] = df[col].astype(float)
    df[col] = standardize_col(df[col])

df.head()

Unnamed: 0        id   host_id zipcode neighbourhood_cleansed  \
0           0  16457286  11796099   11221     Bedford-Stuyvesant   
1           1   1356652   4508795   11233     Bedford-Stuyvesant   
2           2    775016   4088378   11221     Bedford-Stuyvesant   
3           3    773497   4081688   11206     Bedford-Stuyvesant   
4           4   8468835   6518093   11233     Bedford-Stuyvesant   

  property_type  room_type  accommodates  bedrooms      beds  bed_type  price  \
0     Apartment       1.01     -0.448325  -0.22605 -0.524398      1.00   38.0   
1     Apartment       1.01     -0.448325  -0.22605 -0.524398      1.00   90.0   
2     Apartment       1.01     -0.448325  -0.22605 -0.524398      1.01   90.0   
3     Apartment       1.02     -0.984809  -0.22605 -0.524398      1.00  200.0   
4     Apartment       1.01     -0.984809  -0.22605 -0.524398      1.00   50.0   

   number_of_reviews  review_scores_rating  availability_30  minimum_nights  \
0          -0.480161                 100.0         -0.71572        0.050488   
1          -0.480161                  90.0          2.21043       -0.023537   
2          -0.506798                 100.0          2.21043       -0.023537   
3          -0.533434                   NaN          2.21043       -0.029705   
4          -0.480161                  60.0         -0.71572       -0.029705   

   bathrooms  host_is_superhost  host_response_rate  
0  -0.315183                0.0                 0.0  
1  -0.315183                0.0                 0.0  
2  -0.315183                0.0                 0.0  
3  -0.315183                0.0                 0.0  
4  -0.315183                0.0                 0.0

In [5]:
def findAveragePriceStandardize(location):
    return (df[(df.neighbourhood_cleansed == location)])

trainingDataSets = []

# get neighborhoods and create standarized datasets from them
neighborhoods = np.unique(df.neighbourhood_cleansed)
for neighborhood in neighborhoods:
    areaStandardize = findAveragePriceStandardize(neighborhood)
    areaStandardize.drop(['neighbourhood_cleansed'], axis=1)
    trainingDataSets.append(areaStandardize)

modelDataSets = []
targetDataSets = []

#get standardized neighborhoods and create model/target data from them
for dataSet in trainingDataSets:
    modelData  = np.array(dataSet.iloc[:, [7,8,9,16]]).astype('float32')
    target = np.array(dataSet.iloc[:, 11]).astype('float32')
    modelDataSets.append(modelData)
    targetDataSets.append(target)

# areaStandardize = findAveragePriceStandardize('Allerton')
# areaStandardize.drop(['neighbourhood_cleansed'], axis=1)
# areaStandardize.info()


In [6]:
import boto3
import sagemaker
import io
import os
import sagemaker.amazon.common as smac
from sagemaker import get_execution_role
import json

# Create new sagemaker session
sess = sagemaker.Session()

# S3 bucket to export results to
bucket = "airbnb-estimator-sagemaker"
train_data_prefix = "dataset"
model_prefix = "models"

role = get_execution_role()
output_location = 's3://{}/{}/LinearRegression'.format(bucket, model_prefix)

# Use all regions for ML model
containers = {'us-west-2': '174872318107.dkr.ecr.us-west-2.amazonaws.com/linear-learner:latest',
              'us-east-1': '382416733822.dkr.ecr.us-east-1.amazonaws.com/linear-learner:latest',
              'us-east-2': '404615174143.dkr.ecr.us-east-2.amazonaws.com/linear-learner:latest',
              'eu-west-1': '438346466558.dkr.ecr.eu-west-1.amazonaws.com/linear-learner:latest',
              'ap-northeast-1': '351501993468.dkr.ecr.ap-northeast-1.amazonaws.com/linear-learner:latest'}

trainingData = []
for neighborhood in neighborhoods:
    areaStandardize = findAveragePriceStandardize(neighborhood)
    areaStandardize.drop(['neighbourhood_cleansed'], axis=1)

    modelData = np.array(areaStandardize.iloc[:, [7,8,9,16]]).astype('float32')
    target = np.array(areaStandardize.iloc[:, 11]).astype('float32')
        
    # Use the IO buffer as dataset is small
    buf = io.BytesIO()

    smac.write_numpy_to_dense_tensor(buf,modelData,target)
    buf.seek(0)

    # importing create data set and upload to s3
    key = 'linear-regression-{}'.format(neighborhood).replace(' ','-').replace(',','').lower()
    boto3.resource('s3').Bucket(bucket).Object(os.path.join(train_data_prefix, 'train', key)).upload_fileobj(buf)
    trainingData.append('s3://{}/{}/train/{}'.format(bucket, train_data_prefix, key))


In [12]:
trainingData[110]

's3://airbnb-estimator-sagemaker/dataset/train/linear-regression-jamaica'

In [8]:
for dataset in trainingData[193:126:-1]:
    job = dataset.replace('s3://airbnb-estimator-sagemaker/dataset/train/linear-regression-','')
    # create model and train it
    linear = sagemaker.estimator.Estimator(containers[boto3.Session().region_name],
                                        role, 
                                        train_instance_count=1, 
                                        train_instance_type='ml.m4.xlarge',
                                        output_path=output_location,
                                        sagemaker_session=sess,
                                        base_job_name=job.replace("'","").replace(".",""))

    linear.set_hyperparameters(feature_dim=4,
                               predictor_type='regressor',
                               normalize_data=False,
                               mini_batch_size = 2)
    linear.fit({'train': dataset})

2019-05-06 01:40:43 Starting - Starting the training job...
2019-05-06 01:40:45 Starting - Launching requested ML instances.........
2019-05-06 01:42:23 Starting - Preparing the instances for training.........
2019-05-06 01:44:05 Downloading - Downloading input data
2019-05-06 01:44:05 Training - Training image download completed. Training in progress..
Docker entrypoint called with argument(s): train
[05/06/2019 01:44:07 INFO 140540508493632] Reading default configuration from /opt/amazon/lib/python2.7/site-packages/algorithm/default-input.json: {u'loss_insensitivity': u'0.01', u'epochs': u'15', u'init_bias': u'0.0', u'lr_scheduler_factor': u'auto', u'num_calibration_samples': u'10000000', u'accuracy_top_k': u'3', u'_num_kv_servers': u'auto', u'use_bias': u'true', u'num_point_for_scaler': u'10000', u'_log_level': u'info', u'quantile': u'0.5', u'bias_lr_mult': u'auto', u'lr_scheduler_step': u'auto', u'init_method': u'uniform', u'init_sigma': u'0.01', u'lr_scheduler_minimum_lr': u'auto'

#metrics {"Metrics": {"train_mse_objective": {"count": 1, "max": 0.8636354082382424, "sum": 0.8636354082382424, "min": 0.8636354082382424}}, "EndTime": 1557107060.310416, "Dimensions": {"model": 0, "Host": "algo-1", "Operation": "training", "Algorithm": "Linear Learner", "epoch": 1}, "StartTime": 1557107060.31035}

#metrics {"Metrics": {"train_mse_objective": {"count": 1, "max": 0.8556517839822223, "sum": 0.8556517839822223, "min": 0.8556517839822223}}, "EndTime": 1557107060.310499, "Dimensions": {"model": 1, "Host": "algo-1", "Operation": "training", "Algorithm": "Linear Learner", "epoch": 1}, "StartTime": 1557107060.310485}

#metrics {"Metrics": {"train_mse_objective": {"count": 1, "max": 0.8613602611065583, "sum": 0.8613602611065583, "min": 0.8613602611065583}}, "EndTime": 1557107060.310553, "Dimensions": {"model": 2, "Host": "algo-1", "Operation": "training", "Algorithm": "Linear Learner", "epoch": 1}, "StartTime": 1557107060.31054}

#metrics {"Metrics": {"train_mse_objective": {"c

#metrics {"Metrics": {"train_mse_objective": {"count": 1, "max": 0.847875949905289, "sum": 0.847875949905289, "min": 0.847875949905289}}, "EndTime": 1557107071.318358, "Dimensions": {"model": 0, "Host": "algo-1", "Operation": "training", "Algorithm": "Linear Learner", "epoch": 3}, "StartTime": 1557107071.318256}

#metrics {"Metrics": {"train_mse_objective": {"count": 1, "max": 0.8423961709133578, "sum": 0.8423961709133578, "min": 0.8423961709133578}}, "EndTime": 1557107071.318562, "Dimensions": {"model": 1, "Host": "algo-1", "Operation": "training", "Algorithm": "Linear Learner", "epoch": 3}, "StartTime": 1557107071.318534}

#metrics {"Metrics": {"train_mse_objective": {"count": 1, "max": 0.8464111413549167, "sum": 0.8464111413549167, "min": 0.8464111413549167}}, "EndTime": 1557107071.318634, "Dimensions": {"model": 2, "Host": "algo-1", "Operation": "training", "Algorithm": "Linear Learner", "epoch": 3}, "StartTime": 1557107071.318618}

#metrics {"Metrics": {"train_mse_objective": {"co

#metrics {"Metrics": {"train_mse_objective": {"count": 1, "max": 0.8409736710924799, "sum": 0.8409736710924799, "min": 0.8409736710924799}}, "EndTime": 1557107082.806218, "Dimensions": {"model": 0, "Host": "algo-1", "Operation": "training", "Algorithm": "Linear Learner", "epoch": 5}, "StartTime": 1557107082.806154}

#metrics {"Metrics": {"train_mse_objective": {"count": 1, "max": 0.8375587516901754, "sum": 0.8375587516901754, "min": 0.8375587516901754}}, "EndTime": 1557107082.806305, "Dimensions": {"model": 1, "Host": "algo-1", "Operation": "training", "Algorithm": "Linear Learner", "epoch": 5}, "StartTime": 1557107082.806287}

#metrics {"Metrics": {"train_mse_objective": {"count": 1, "max": 0.8397819405311523, "sum": 0.8397819405311523, "min": 0.8397819405311523}}, "EndTime": 1557107082.806368, "Dimensions": {"model": 2, "Host": "algo-1", "Operation": "training", "Algorithm": "Linear Learner", "epoch": 5}, "StartTime": 1557107082.806351}

#metrics {"Metrics": {"train_mse_objective": {

#metrics {"Metrics": {"train_mse_objective": {"count": 1, "max": 0.8362539547966577, "sum": 0.8362539547966577, "min": 0.8362539547966577}}, "EndTime": 1557107093.60837, "Dimensions": {"model": 0, "Host": "algo-1", "Operation": "training", "Algorithm": "Linear Learner", "epoch": 7}, "StartTime": 1557107093.608306}

#metrics {"Metrics": {"train_mse_objective": {"count": 1, "max": 0.8350633179362199, "sum": 0.8350633179362199, "min": 0.8350633179362199}}, "EndTime": 1557107093.60846, "Dimensions": {"model": 1, "Host": "algo-1", "Operation": "training", "Algorithm": "Linear Learner", "epoch": 7}, "StartTime": 1557107093.608442}

#metrics {"Metrics": {"train_mse_objective": {"count": 1, "max": 0.8351906037036781, "sum": 0.8351906037036781, "min": 0.8351906037036781}}, "EndTime": 1557107093.60852, "Dimensions": {"model": 2, "Host": "algo-1", "Operation": "training", "Algorithm": "Linear Learner", "epoch": 7}, "StartTime": 1557107093.608504}

#metrics {"Metrics": {"train_mse_objective": {"co

...

#metrics {"Metrics": {"train_mse_objective": {"count": 1, "max": 0.9097888985149111, "sum": 0.9097888985149111, "min": 0.9097888985149111}}, "EndTime": 1557120637.425044, "Dimensions": {"model": 0, "Host": "algo-1", "Operation": "training", "Algorithm": "Linear Learner", "epoch": 4}, "StartTime": 1557120637.424953}

#metrics {"Metrics": {"train_mse_objective": {"count": 1, "max": 0.921745125005301, "sum": 0.921745125005301, "min": 0.921745125005301}}, "EndTime": 1557120637.425152, "Dimensions": {"model": 1, "Host": "algo-1", "Operation": "training", "Algorithm": "Linear Learner", "epoch": 4}, "StartTime": 1557120637.425132}

#metrics {"Metrics": {"train_mse_objective": {"count": 1, "max": 0.9104378639221705, "sum": 0.9104378639221705, "min": 0.9104378639221705}}, "EndTime": 1557120637.425209, "Dimensions": {"model": 2, "Host": "algo-1", "Operation": "training", "Algorithm": "Linear Learner", "epoch": 4}, "StartTime": 1557120637.425195}

#metrics {"Metrics": {"train_mse_objective": {"co

#metrics {"Metrics": {"train_mse_objective": {"count": 1, "max": 0.9097819385429353, "sum": 0.9097819385429353, "min": 0.9097819385429353}}, "EndTime": 1557120675.850748, "Dimensions": {"model": 0, "Host": "algo-1", "Operation": "training", "Algorithm": "Linear Learner", "epoch": 5}, "StartTime": 1557120675.850643}

#metrics {"Metrics": {"train_mse_objective": {"count": 1, "max": 0.9199289363893369, "sum": 0.9199289363893369, "min": 0.9199289363893369}}, "EndTime": 1557120675.850849, "Dimensions": {"model": 1, "Host": "algo-1", "Operation": "training", "Algorithm": "Linear Learner", "epoch": 5}, "StartTime": 1557120675.850834}

#metrics {"Metrics": {"train_mse_objective": {"count": 1, "max": 0.9103931123871389, "sum": 0.9103931123871389, "min": 0.9103931123871389}}, "EndTime": 1557120675.850906, "Dimensions": {"model": 2, "Host": "algo-1", "Operation": "training", "Algorithm": "Linear Learner", "epoch": 5}, "StartTime": 1557120675.850891}

#metrics {"Metrics": {"train_mse_objective": {

#metrics {"Metrics": {"train_mse_objective": {"count": 1, "max": 0.909775365655552, "sum": 0.909775365655552, "min": 0.909775365655552}}, "EndTime": 1557120714.25193, "Dimensions": {"model": 0, "Host": "algo-1", "Operation": "training", "Algorithm": "Linear Learner", "epoch": 6}, "StartTime": 1557120714.251853}

#metrics {"Metrics": {"train_mse_objective": {"count": 1, "max": 0.918323608709297, "sum": 0.918323608709297, "min": 0.918323608709297}}, "EndTime": 1557120714.252031, "Dimensions": {"model": 1, "Host": "algo-1", "Operation": "training", "Algorithm": "Linear Learner", "epoch": 6}, "StartTime": 1557120714.252013}

#metrics {"Metrics": {"train_mse_objective": {"count": 1, "max": 0.910352261038587, "sum": 0.910352261038587, "min": 0.910352261038587}}, "EndTime": 1557120714.252087, "Dimensions": {"model": 2, "Host": "algo-1", "Operation": "training", "Algorithm": "Linear Learner", "epoch": 6}, "StartTime": 1557120714.252073}

#metrics {"Metrics": {"train_mse_objective": {"count": 1


2019-05-06 05:32:35 Uploading - Uploading generated training model
2019-05-06 05:32:35 Completed - Training job completed
Billable seconds: 364
2019-05-06 05:32:52 Starting - Starting the training job...
2019-05-06 05:32:57 Starting - Launching requested ML instances......

KeyboardInterrupt: 

In [ ]:
# modelData = np.array(areaStandardize.iloc[:, [7,8,9,16]]).astype('float32')
# target = np.array(areaStandardize.iloc[:, 11]).astype('float32')

In [ ]:
# import boto3
# import sagemaker
# import io
# import os
# import sagemaker.amazon.common as smac

# # Create new sagemaker session
# sess = sagemaker.Session()

# # S3 bucket to export results to
# bucket = "airbnb-estimator-sagemaker"
# train_data_prefix = "dataset"
# model_prefix = "models"
    
# # Use the IO buffer as dataset is small
# buf = io.BytesIO()

# smac.write_numpy_to_dense_tensor(buf,modelData,target)
# buf.seek(0)

# # importing linearyLerner
# key = 'linear-regression-harlem'
# boto3.resource('s3').Bucket(bucket).Object(os.path.join(train_data_prefix, 'train', key)).upload_fileobj(buf)
# s3_train_data = 's3://{}/{}/train/{}'.format(bucket, train_data_prefix, key)

# print('uploaded training data location: {}'.format(s3_train_data))
# output_location = 's3://{}/{}/LinearRegression'.format(bucket, model_prefix)

# print('training artifacts will be uploaded to: {}'.format(output_location))
# # Use all regions for ML model
# containers = {'us-west-2': '174872318107.dkr.ecr.us-west-2.amazonaws.com/linear-learner:latest',
#               'us-east-1': '382416733822.dkr.ecr.us-east-1.amazonaws.com/linear-learner:latest',
#               'us-east-2': '404615174143.dkr.ecr.us-east-2.amazonaws.com/linear-learner:latest',
#               'eu-west-1': '438346466558.dkr.ecr.eu-west-1.amazonaws.com/linear-learner:latest',
#               'ap-northeast-1': '351501993468.dkr.ecr.ap-northeast-1.amazonaws.com/linear-learner:latest'}

In [ ]:
from sagemaker import get_execution_role
import json

s3_train_data = 's3://airbnb-estimator-sagemaker/dataset/train/linear-regression-allerton'
role = get_execution_role()
# linear = sagemaker.estimator.Estimator(containers[boto3.Session().region_name],
#                                     role, 
#                                     train_instance_count=1, 
#                                     train_instance_type='ml.m4.xlarge',
#                                     output_path=output_location,
#                                     sagemaker_session=sess,
#                                     base_job_name='allerton')

# linear.set_hyperparameters(feature_dim=4,
#                            predictor_type='regressor',
#                            normalize_data=False,
#                            mini_batch_size = 5)
# linear.fit({'train': s3_train_data})

# linear_predictor = linear.deploy(initial_instance_count=1,
#                                  instance_type='ml.t2.medium',
#                                  endpoint_name='linear-regression',
#                                  update_endpoint=True
#                                  )


In [ ]:
# sagemaker.Session().delete_endpoint(linear_predictor.endpoint)